In [1]:
!python setup.py build_ext --inplace

running build_ext
running build_ext


In [2]:
import network_simulation_combined as net_sims
import popconstruct_hyperdirect as pops
import plotting_helper_functions as plt_help
import pipeline_creation as pl_creat
import pandas as pd
import os
import time
import pdb

import pylab as pl
import pickle
import numpy as np
import pandas as pd
import pingouin
import sklearn 

def saveresults_vars(variable, prefix):
    pickle.dump(variable, open(prefix, 'wb'))
    
def loadresults_vars(prefix):
    return pickle.load(open(prefix, "rb"))

data_dir = "./Data/weights_analysis/GPeA_dSPN-iSPN/"
figure_dir = "./Figures/weights_analysis/"

2023-08-31 21:17:04,328	INFO worker.py:1352 -- Connecting to existing Ray cluster at address: 127.0.0.1:6379...
2023-08-31 21:17:04,335	INFO worker.py:1529 -- Connected to Ray cluster. View the dashboard at http://127.0.0.1:8265 


In [3]:
experimentchoice = 'stopsignal'
number_of_choices = 1
#pl_creat.choose_pipeline(experimentchoice)

In [4]:
environment = {
    
    'experimentchoice': experimentchoice,
    'inter_trial_interval': None,
    'thalamic_threshold': 30.,
    'movement_time': ['constant', 300], #['constant', 300], #default sampled from N(250,1.5), ["constant",250], ["mean",250]
    'choice_timeout': 300, #default 1000
    
    'params': None, #neuron parameters (init_params.py)
    'pops': None,   #population parameters (init_params.py)
    'receps' : None, #receptor parameters (init_params.py)
    'base' : None, #baseline stimulation parameters (init_params.py)
    'dpmns' : None, #dopamine related parameters (init_params.py)
    'd1' : None, #D1-MSNs population related parameters (init_params.py)
    'd2' : None, #D2-MSNs population related parameters (init_params.py)
    'channels' : pd.DataFrame([["left"]], columns=['action']), #action channels related parameters (init_params.py)
    'number_of_choices':number_of_choices,
    #'actionchannels' : pd.DataFrame([[1],[2]], columns=['action']), #labels for the actions (init_params.py)
    #'actionchannels' : pd.DataFrame([["left"],["right"]], columns=['action']), #labels for the actions (init_params.py)
    'newpathways' : None, #connectivity parameters (popconstruct.py)
    'Q_support_params': None, #initialization of Q-values update (qvalues.py) 
    'Q_df_set': pd.DataFrame([[0.5]],columns=["left"]), #pd.DataFrame([[0.3,0.7]],columns=['left','right']), #initialized Q-values df (qvalues.py)  
    'n_trials': 30, #number of trials (generateepochs.py)
    'volatility': [None,"exact"], #frequency of changepoints (generateepochs.py)
    'conflict': (1.0), #probability of the preferred choice (generateepochs.py)
    'reward_mu': 1, #mean for the magnitude of the reward (generateepochs.py)
    'reward_std': 0.1, #std for the magnitude of the reward (generateepochs.py)
    'maxstim': 1.15, # amplitude of the cortical input over base line #0.85
    'sustainedfraction': 0.75,
    
    #Stop 1
    'stop_signal_present': True,
    'stop_signal_probability': 1., #probability of trials that will get the stop signal / list of trial numbers
    'stop_signal_amplitude': 0.4, # amplitude of the stop signal over base line
    'stop_signal_onset': 70., #in ms #antes 200
    'stop_signal_duration' : 145., 
    'stop_signal_channel': "all", #"all" (all channels are given the stop signal) 
                                #/"any" (channel given the stop signal is chosen randomly)
                                # [list of channels] == subset of channels given the stop signa
    'stop_signal_population':["STNE"],
    
    #Stop 2
    'stop_2_signal_present': True,
    'stop_2_signal_probability': 1., #probability of trials that will get the stop signal / list of trial numbers
    'stop_2_signal_amplitude': 0.4, # amplitude of the stop signal over base line
    'stop_2_signal_onset': 70., #in ms #antes 200
    'stop_2_signal_duration' : 145.,
    'stop_2_signal_channel': "all", #"all" (all channels are given the stop signal) 
                                #/"any" (channel given the stop signal is chosen randomly)
                                # [list of channels] == subset of channels given the stop signal
    'stop_2_signal_population':["GPeA"],                           
    
    
    'decision_channel' : 'all', #'all'(all channels)
                              # '0' : left channel considered 
                              # '1' : right channel considered
    
    'record_variables': [], #["weight","optogenetic_input", "stop_input_1", "stop_input_2"],
    
    #Opto
    'opt_signal_present': True,
    'opt_signal_probability': 1., #[0,1,2,3,4], # probability of trials that will get the optogenetic signal / list of trial numbers
    'opt_signal_amplitude': 0.4, # ampitude of the stop signal over base line
    'opt_signal_onset': 70., # in ms
    'opt_signal_duration': 145.,
    'opt_signal_channel': "all", # "all" (all channels are given the stop signal) 
    'opt_signal_population':["D2STR"],    
}

In [5]:
seeds = 0 #np.random.randint(0,9999999)
print(seeds)
offset = 0 #To start from last sim run (remember number of last sim) 

0


In [6]:
connections =  pops.helper_poppathways(None,None)

channels: one
scaling_conn 1
scaling_wts 2.0


In [7]:
connections.loc[connections['src'] == 'GPeA'][['src', 'dest', 'receptor', 'type', 'con', 'eff', 'plastic']]

src    dest receptor  type   con    eff plastic
23  GPeA`    FSI`    GABA`  all`  0.4`  0.02`  False`
24  GPeA`  D2STR`    GABA`  syn`  0.4`  0.12`  False`
25  GPeA`  D1STR`    GABA`  syn`  0.4`  0.32`  False`
26  GPeA`   GPeA`    GABA`  all`  0.4`   0.3`  False`

In [8]:
solutions_1 = np.arange(0.02, 0.44, 0.05) #np.arange(0.42, 0.63, 0.1)
solutions_2 =  np.arange(0.02, 0.64, 0.05) #np.arange(0.02, 0.64, 0.1) #np.arange(0.02, 0.63, 0.1)
params_to_fit_1 = ['GPeA', 'D1STR', 'GABA', 'syn', 0.4, 0.32, False]
params_to_fit_2 = ['GPeA', 'D2STR', 'GABA', 'syn', 0.4, 0.12, False]
print(solutions_1)
print(solutions_2)

[0.02 0.07 0.12 0.17 0.22 0.27 0.32 0.37 0.42]
[0.02 0.07 0.12 0.17 0.22 0.27 0.32 0.37 0.42 0.47 0.52 0.57 0.62]


In [9]:
for i in np.arange(len(solutions_1)):
    if i < offset:
        continue
    print("i",i)

    val_1 = solutions_1[i]
    
    for j in np.arange(len(solutions_2)):
        
        val_2 = solutions_2[j]
        
        seed_1 = i
        seed_2 = j
        
        if os.path.exists(data_dir+'network_data_GPeA-dSPN-iSPN_iSPN+STN+GPeA_'+str(seed_1)+'_'+str(seed_2)):
            continue
        
        new_params =  connections.copy() 
        
        ind_1 = new_params[(new_params["src"] == params_to_fit_1[0])&(new_params["dest"] == params_to_fit_1[1])&(new_params["receptor"] == params_to_fit_1[2])&(new_params["type"] == params_to_fit_1[3])&(new_params["con"] == params_to_fit_1[4])].index.tolist()
        new_params.loc[ind_1[0], "eff"] = val_1

        ind_2 = new_params[(new_params["src"] == params_to_fit_2[0])&(new_params["dest"] == params_to_fit_2[1])&(new_params["receptor"] == params_to_fit_2[2])&(new_params["type"] == params_to_fit_2[3])&(new_params["con"] == params_to_fit_2[4])].index.tolist()
        new_params.loc[ind_2[0], "eff"] = val_2
        
        new_env = environment.copy()
        new_env['newpathways'] = new_params
        
        print('dSPN - seed 1:', seed_1, ', weight:', val_1)
        print('iSPN - seed 2:', seed_2, ', weight:', val_2)

        results = net_sims.run_simulation(seed_1, seed_2, new_env)

i 0
i 1
i 2
i 3
i 4
i 5
i 6
i 7
dSPN - seed 1: 7 , weight: 0.37000000000000005
iSPN - seed 2: 6 , weight: 0.32000000000000006
{'experimentchoice': 'stopsignal', 'inter_trial_interval': None, 'thalamic_threshold': 30.0, 'movement_time': ['constant', 300], 'choice_timeout': 300, 'params': None, 'pops': None, 'receps': None, 'base': None, 'dpmns': None, 'd1': None, 'd2': None, 'channels':   action
0   left, 'number_of_choices': 1, 'newpathways':        src    dest receptor  type        con      eff plastic  \
0     LIP`  D1STR`    AMPA`  syn`       1.0`   0.022`   True`   
1     LIP`  D1STR`    NMDA`  syn`       1.0`    0.03`  False`   
2     LIP`  D2STR`    AMPA`  syn`       1.0`   0.022`   True`   
3     LIP`  D2STR`    NMDA`  syn`       1.0`   0.028`  False`   
4     LIP`    FSI`    AMPA`  all`       1.0`    0.17`  False`   
5     LIP`     Th`    AMPA`  syn`       1.0`   0.025`  False`   
6     LIP`     Th`    NMDA`  syn`       1.0`   0.029`  False`   
7   D1STR`  D1STR`    GABA`  syn`

(worker pid=3012) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3005) in choose pipeline
(worker pid=3007) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3005) in choose pipeline
(worker pid=3005) in choose pipeline
(worker pid=3012) in choose pipeline
(worker pid=3004) in choose pipeline
(worker pid=3007) in choose pipeline
(worker pid=3007) in choose pipeline
(worker pid=3006) in choose pipeline
(worker pid=3005) in choose pipeline
(worker pid=3004) in choose pipeline
(worker pid=3007) in choose pipeline
(worker pid=3015) in choose pipeline
(worker pid=3015) in choose pipeline
SpawnThreadManagers <backend.Pipeline object at 0x7f8438967ee0>
SpawnThreadManagers <backend.Pipeline object at 0x7f8438967ee0>
SpawnThreadManagers <backend.Pipeline object at 0x7f8438967ee0>
SpawnThreadManagers <backend.Pipeline object at 0x7f8438967ee0>
Spaw

SpawnThreadManagers <backend.Pipeline object at 0x7f8438ba76a0>
(worker pid=3007) [ 6 14 15  7  1  9 20  5 21 12  0 23  4 19 22 10 17 18 27 16 26 11 25  3
(worker pid=3007)   2 29 13  8 28 24]
(worker pid=3003) [ 2 28 13 10 26 24 27 11 17 22  5 16  8 14 23 20  1 29  6  4 18 19  9  7
(worker pid=3003)  25  3  0 21 15 12]
(worker pid=3003) [ 5 16 20  6 13  8 11 12  2 25 26  4 10 23 28  9  1 27  7 14 21 22 19 17
(worker pid=3003)  24  3 18  0 29 15]
(worker pid=3034) [ 7 28 25  3 13 29  2 12  8 23 11 19 20 14  5 21  0 17 10  9 22  6 16 18
(worker pid=3034)  24  1 26  4 15 27]
SpawnThreadManagers <backend.Pipeline object at 0x7f8438ba76a0>
SpawnThreadManagers <backend.Pipeline object at 0x7f8438ba76a0>
(worker pid=3003) [ 5 16 20  6 13  8 11 12  2 25 26  4 10 23 28  9  1 27  7 14 21 22 19 17
(worker pid=3003)  24  3 18  0 29 15]
(worker pid=3003) [24 27 21 25 14 12 19 23 29 16  0 13  2 11 18 28  3 22  7 26  1 10  9  4
(worker pid=3003)  15 17 20  8  6  5]
(worker pid=3034) [ 7 28 25  3 13 

(worker pid=3006) gateFRs [30.88888889]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3006) gateFRs [30.88888889]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3007) gateFRs [28.66666667]
(worker pid=3007) thresholds_crossed []
(worker pid=3007) gateFRs [28.66666667]
(worker pid=3007) thresholds_crossed []
(worker pid=3034) gateFRs [30.66666667]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3034) gateFRs [30.66666667]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3033) gateFRs [30.88888889]
(worker pid=3033) thresholds_crossed [0]
(worker pid=3033) gateFRs [30.88888889]
(worker pid=3033) thresholds_crossed [0]
(worker pid=3042) gateFRs [30.66666667]
(worker pid=3042) thresholds_crossed [0]
(worker pid=3042) gateFRs [30.66666667]
(worker pid=3042) thresholds_crossed [0]
(worker pid=3037) gateFRs [30.66666667]
(worker pid=3037) thresholds_crossed [0]
(worker pid=3037) gateFRs [30.66666667]
(worker pid=3037) thresholds_crossed [0]
(worker pid=3006) trial_num 0


(worker pid=3007) stop stim started
(worker pid=3007) stop_2 stim started
(worker pid=3007) opt stim started
(worker pid=3007) stop stim started
(worker pid=3007) stop_2 stim started
(worker pid=3007) opt stim started
(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) gateFRs [30.22222222]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3034) gateFRs [30.22222222]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(

...

(worker pid=3033) gateFRs [22.88888889]
(worker pid=3033) thresholds_crossed []
(worker pid=3033) gateFRs [22.88888889]
(worker pid=3033) thresholds_crossed []
(worker pid=3033) trial_num 14
(worker pid=3033)   action
(worker pid=3033) 0   left
(worker pid=3033) chosen_action: stop
(worker pid=3033) trial_num 14
(worker pid=3033)   action
(worker pid=3033) 0   left
(worker pid=3033) chosen_action: stop
(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3006) gateFRs [30.22222222]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3006) gateFRs [30.22222222]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim star

(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3006) stop stim started
(worker pid=3006) stop_2 stim started
(worker pid=3006) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3006) gateFRs [28.]
(worker pid=3006) thresholds_crossed []
(worker pid=3006) gateFRs [28.]
(worker pid=3006) thresholds_crossed []
(worker pid=3033) gateFRs [23.55555556]
(worker pid=3033) thresholds_crossed []
(worker pid=3033) gateFRs [23.55555556]
(worker pid=3033) thresholds_crossed []
(worker pid=3034) gateFRs [30.66666667]
(w

(worker pid=3006) gateFRs [30.44444444]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3006) gateFRs [30.44444444]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3033) gateFRs [28.]
(worker pid=3033) thresholds_crossed []
(worker pid=3033) gateFRs [28.]
(worker pid=3033) thresholds_crossed []
(worker pid=3006) trial_num 20
(worker pid=3006)   action
(worker pid=3006) 0   left
(worker pid=3006) chosen_action: left
(worker pid=3006) trial_num 20
(worker pid=3006)   action
(worker pid=3006) 0   left
(worker pid=3006) chosen_action: left
(worker pid=3033) trial_num 21
(worker pid=3033)   action
(worker pid=3033) 0   left
(worker pid=3033) chosen_action: stop
(worker pid=3033) trial_num 21
(worker pid=3033)   action
(worker pid=3033) 0   left
(worker pid=3033) chosen_action: stop
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) o

(worker pid=3006) gateFRs [30.22222222]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3006) gateFRs [30.22222222]
(worker pid=3006) thresholds_crossed [0]
(worker pid=3006) trial_num 23
(worker pid=3006)   action
(worker pid=3006) 0   left
(worker pid=3006) chosen_action: left
(worker pid=3006) trial_num 23
(worker pid=3006)   action
(worker pid=3006) 0   left
(worker pid=3006) chosen_action: left
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3034) gateFRs [30.22222222]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3034) gateFRs [30.22222222]
(worker pid=3034) thresholds_crosse

(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3033) stop stim started
(worker pid=3033) stop_2 stim started
(worker pid=3033) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) stop stim started
(worker pid=3034) stop_2 stim started
(worker pid=3034) opt stim started
(worker pid=3034) gateFRs [30.66666667]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3034) gateFRs [30.66666667]
(worker pid=3034) thresholds_crossed [0]
(worker pid=3033) gateFRs [30.66666667]
(worker pid=3033) thresholds_crossed [0]
(worker pid=3033) gateFRs [30.66666667]
(worker pid=3033) thresholds_crossed [0]
(worker pid=3034) trial_num 28
(worker pid=3034)   action
(worker pid=3034) 0   left
(worker pid=3034) chosen_action: left
(worker pid=3034) trial_num 28
(worker pid=3034)   action
(worker pid=3034) 0   left
(worker pid=3034) chosen_action: